In [1]:
import nltk
nltk.download('vader_lexicon')

from nltk.sentiment.vader import SentimentIntensityAnalyzer

sentences = ["VADER is smart, handsome, and funny.", # positive sentence example
    "VADER is smart, handsome, and funny!", # punctuation emphasis handled correctly (sentiment intensity adjusted)
    "VADER is very smart, handsome, and funny.",  # booster words handled correctly (sentiment intensity adjusted)
    "VADER is VERY SMART, handsome, and FUNNY.",  # emphasis for ALLCAPS handled
    "VADER is VERY SMART, handsome, and FUNNY!!!",# combination of signals - VADER appropriately adjusts intensity
    "VADER is VERY SMART, really handsome, and INCREDIBLY FUNNY!!!",# booster words & punctuation make this close to ceiling for score
    "The book was good.",         # positive sentence
    "The book was kind of good.", # qualified positive sentence is handled correctly (intensity adjusted)
    "The plot was good, but the characters are uncompelling and the dialog is not great.", # mixed negation sentence
    "A really bad, horrible book.",       # negative sentence with booster words
    "At least it isn't a horrible book.", # negated negative sentence with contraction
    ":) and :D",     # emoticons handled
    "",              # an empty string is correctly handled
    "Today sux",     #  negative slang handled
    "Today sux!",    #  negative slang with punctuation emphasis handled
    "Today SUX!",    #  negative slang with capitalization emphasis
    "Today kinda sux! But I'll get by, lol" # mixed sentiment example with slang and constrastive conjunction "but"
]

for sentence in sentences:
    sid = SentimentIntensityAnalyzer()
    print(sentence)
    ss = sid.polarity_scores(sentence)
    for k in sorted(ss):
        print('{0}: {1}, '.format(k, ss[k]), end='')
    print()

VADER is smart, handsome, and funny.
compound: 0.8316, neg: 0.0, neu: 0.254, pos: 0.746, 
VADER is smart, handsome, and funny!
compound: 0.8439, neg: 0.0, neu: 0.248, pos: 0.752, 
VADER is very smart, handsome, and funny.
compound: 0.8545, neg: 0.0, neu: 0.299, pos: 0.701, 
VADER is VERY SMART, handsome, and FUNNY.
compound: 0.9227, neg: 0.0, neu: 0.246, pos: 0.754, 
VADER is VERY SMART, handsome, and FUNNY!!!
compound: 0.9342, neg: 0.0, neu: 0.233, pos: 0.767, 
VADER is VERY SMART, really handsome, and INCREDIBLY FUNNY!!!
compound: 0.9469, neg: 0.0, neu: 0.294, pos: 0.706, 
The book was good.
compound: 0.4404, neg: 0.0, neu: 0.508, pos: 0.492, 
The book was kind of good.
compound: 0.3832, neg: 0.0, neu: 0.657, pos: 0.343, 
The plot was good, but the characters are uncompelling and the dialog is not great.
compound: -0.7042, neg: 0.327, neu: 0.579, pos: 0.094, 
A really bad, horrible book.
compound: -0.8211, neg: 0.791, neu: 0.209, pos: 0.0, 
At least it isn't a horrible book.
compound

[nltk_data] Downloading package vader_lexicon to
[nltk_data]     /home/xie/nltk_data...
[nltk_data]   Package vader_lexicon is already up-to-date!


In [47]:
# Allows user input for data set to label emotions
dataset_name = input('Dataset to label emotions (google, msr, quora, mix, twit0.825):  ')

if not (dataset_name.lower() in ['google', 'msr', 'quora', 'mix', 'twit0.825']): 
    print('Please enter a valid dataset name')

print('Dataset selected: ' + dataset_name)

training_stats = {'dataset name': dataset_name + '-training'}
eval_stats = {'dataset name': dataset_name + '-testing'}

Dataset to label emotions (google, msr, quora, mix, twit0.825):  mix
Dataset selected: mix


In [48]:
import numpy as np
import pandas as pd

train_df = pd.read_csv(f'compiled-data/{dataset_name}/{dataset_name}-training_emolabel.tsv', sep="\t").astype(str)
training_stats.update({'dataset size': train_df.size})

input_sids = []
target_sids = []

for index, row in train_df.iterrows():
    if (index %1000 == 0): 
        print ("Processing " + str(index))

    i_text = (row.input_text[:512] + '..') if len(row.input_text) > 512 else row.input_text
    t_text = (row.target_text[:512] + '..') if len(row.target_text) > 512 else row.target_text

    input_sid = SentimentIntensityAnalyzer()
    input_ss = input_sid.polarity_scores(i_text)

    target_sid = SentimentIntensityAnalyzer()
    target_ss = target_sid.polarity_scores(t_text)
    
    input_sids.append (input_ss['compound'])
    target_sids.append (target_ss['compound'])
    
train_df["input_sid"] = input_sids
train_df["target_sid"] = target_sids
train_df = train_df[train_df['input_emo'] != "nan"]
train_df = train_df[train_df['target_emo'] != "nan"]
train_df = train_df.drop(['Unnamed: 0'], axis=1)
train_df = train_df.drop(['Unnamed: 0.1'], axis=1)
train_df = train_df.drop(['Unnamed: 0.1.1'], axis=1)
train_df = train_df.drop(['input_score'], axis=1)
train_df = train_df.drop(['target_score'], axis=1)
train_df.to_csv(f'compiled-data/{dataset_name}/{dataset_name}-training_emolabel_s.tsv', sep="\t")

training_stats.update({'dataset size after nan emotion removal': train_df.size})

Processing 0
Processing 1000
Processing 2000
Processing 3000
Processing 4000
Processing 5000
Processing 6000
Processing 7000
Processing 8000
Processing 9000
Processing 10000
Processing 11000
Processing 12000
Processing 13000
Processing 14000
Processing 15000
Processing 16000
Processing 17000
Processing 18000
Processing 19000
Processing 20000
Processing 21000
Processing 22000
Processing 23000
Processing 24000
Processing 25000
Processing 26000
Processing 27000
Processing 28000
Processing 29000
Processing 30000
Processing 31000
Processing 32000
Processing 33000
Processing 34000
Processing 35000
Processing 36000
Processing 37000
Processing 38000
Processing 39000
Processing 40000
Processing 41000
Processing 42000
Processing 43000
Processing 44000
Processing 45000
Processing 46000
Processing 47000
Processing 48000
Processing 49000
Processing 50000
Processing 51000
Processing 52000
Processing 53000
Processing 54000
Processing 55000
Processing 56000
Processing 57000
Processing 58000
Processing

In [49]:
import numpy as np
import pandas as pd

eval_df = pd.read_csv(f'compiled-data/{dataset_name}/{dataset_name}-testing_emolabel.tsv', sep="\t").astype(str)
eval_stats.update({'dataset size': eval_df.size})

input_sids = []
target_sids = []

for index, row in eval_df.iterrows():
    if (index %1000 == 0): 
        print ("Processing " + str(index))

    i_text = (row.input_text[:512] + '..') if len(row.input_text) > 512 else row.input_text
    t_text = (row.target_text[:512] + '..') if len(row.target_text) > 512 else row.target_text

    input_sid = SentimentIntensityAnalyzer()
    input_ss = input_sid.polarity_scores(i_text)

    target_sid = SentimentIntensityAnalyzer()
    target_ss = target_sid.polarity_scores(t_text)
    
    input_sids.append (input_ss['compound'])
    target_sids.append (target_ss['compound'])
    
eval_df["input_sid"] = input_sids
eval_df["target_sid"] = target_sids 
eval_df = eval_df[eval_df['input_emo'] != "nan"]
eval_df = eval_df[eval_df['target_emo'] != "nan"]
eval_df = eval_df.drop(['Unnamed: 0'], axis=1)
eval_df = eval_df.drop(['Unnamed: 0.1'], axis=1)
eval_df = eval_df.drop(['Unnamed: 0.1.1'], axis=1)
eval_df = eval_df.drop(['input_score'], axis=1)
eval_df = eval_df.drop(['target_score'], axis=1)
eval_df.to_csv(f'compiled-data/{dataset_name}/{dataset_name}-testing_emolabel_s.tsv', sep="\t")

eval_stats.update({'dataset size after nan emotion removal': eval_df.size})

Processing 0
Processing 1000
Processing 2000
Processing 3000
Processing 4000
Processing 5000
Processing 6000
Processing 7000
Processing 8000
Processing 9000
Processing 10000
Processing 11000
Processing 12000
Processing 13000
Processing 14000
Processing 15000
Processing 16000
Processing 17000
Processing 18000
Processing 19000
Processing 20000
Processing 21000
Processing 22000
Processing 23000
Processing 24000
Processing 25000
Processing 26000
Processing 27000
Processing 28000
Processing 29000
Processing 30000
Processing 31000
Processing 32000
Processing 33000
Processing 34000
Processing 35000
Processing 36000
Processing 37000
Processing 38000
Processing 39000
Processing 40000
Processing 41000
Processing 42000
Processing 43000
Processing 44000
Processing 45000
Processing 46000


In [50]:
pos_inconsistency = 0 
neg_inconsistency = 0 
for index, row in train_df.iterrows():
    if (row.input_emo_g == 'positive') & (float(row.input_sid) < 0.0):
        pos_inconsistency += 1
    if (row.input_emo_g == 'negative') & (float(row.input_sid) > 0.0):
        neg_inconsistency += 1
        
with open(f'compiled-data/{dataset_name}/{dataset_name}-training_emo_si_stats.txt', 'w') as f:
    f.write('\n')
    f.write('# of positive emotion with negative sentiment score: ' + str(pos_inconsistency) + ' out of ' + str(train_df.size))
    f.write('\n')
    f.write('# of negative emotion with positive sentiment score: ' + str(neg_inconsistency) + ' out of ' + str(train_df.size))
    f.write('\n')

training_stats.update({'# of positive emotion with negative sentiment score': pos_inconsistency})
training_stats.update({'# of negative emotion with positive sentiment score': neg_inconsistency})

#print('# of positive emotion with negative sentiment score: ' + str(pos_inconsistency))
#print('# of negative emotion with positive sentiment score: ' + str(neg_inconsistency))

In [51]:
pos_inconsistency = 0 
neg_inconsistency = 0 
for index, row in eval_df.iterrows():
    if (row.input_emo_g == 'positive') & (float(row.input_sid) < 0.0):
        pos_inconsistency += 1
    if (row.input_emo_g == 'negative') & (float(row.input_sid) > 0.0):
        neg_inconsistency += 1
        
with open(f'compiled-data/{dataset_name}/{dataset_name}-testing_emo_si_stats.txt', 'w') as f:
    f.write('\n')
    f.write('# of positive emotion with negative sentiment score: ' + str(pos_inconsistency) + ' out of ' + str(eval_df.size))
    f.write('\n')
    f.write('# of negative emotion with positive sentiment score: ' + str(neg_inconsistency) + ' out of ' + str(eval_df.size))
    f.write('\n')

eval_stats.update({'# of positive emotion with negative sentiment score': pos_inconsistency})
eval_stats.update({'# of negative emotion with positive sentiment score': neg_inconsistency})

#print('# of positive emotion with negative sentiment score: ' + str(pos_inconsistency))
#print('# of negative emotion with positive sentiment score: ' + str(neg_inconsistency))

In [52]:
count_p = 0 

for index, row in train_df.iterrows():
    if (row.input_emo_g == 'positive') & (row.target_emo_g == 'positive'):
        if (row.input_emo != row.target_emo):
            diff = float(row.target_sid) - float(row.input_sid) 
            if (diff != 0.0): 
                print(row)
                print(diff)
                print('\n')
                count_p += 1 

count_n = 0
for index, row in train_df.iterrows():
    if (row.input_emo_g == 'negative') & (row.target_emo_g == 'negative'):
        if (row.input_emo != row.target_emo):
            diff = float(row.target_sid) - float(row.input_sid) 
            if (diff != 0.0): 
                print(row)
                print(diff)
                print('\n')
                count_n += 1 

count_a = 0
for index, row in train_df.iterrows():
    if (row.input_emo_g == 'ambiguous') & (row.target_emo_g == 'ambiguous'):
        if (row.input_emo != row.target_emo):
            diff = float(row.target_sid) - float(row.input_sid) 
            if (diff != 0.0): 
                print(row)
                print(diff)
                print('\n')
                count_a += 1 

count_e = 0
for index, row in train_df.iterrows():
    if (row.input_emo_g == 'neutral') & (row.target_emo_g == 'neutral'):
        if (row.input_emo != row.target_emo):
            diff = float(row.target_sid) - float(row.input_sid) 
            if (diff != 0.0): 
                print(row)
                print(diff)
                print('\n')
                count_e += 1 

with open(f'compiled-data/{dataset_name}/{dataset_name}-training_emo_si_stats.txt', 'a') as f:
    f.write('\n')
    f.write('# of Postive Input and Target Labels with Different Sentiment Scores: ' + str(count_p))
    f.write('\n')
    f.write('# of Negative Input and Target Labels with Different Sentiment Scores: ' + str(count_n))
    f.write('\n')
    f.write('# of Ambiguous Input and Target Labels with Different Sentiment Scores: ' + str(count_a))
    f.write('\n')
    f.write('# of Neutral Input and Target Labels with Different Sentiment Scores: ' + str(count_e))
    f.write('\n')

training_stats.update({'# of postive Input and Target Labels with Different Sentiment Scores': count_p})
training_stats.update({'# of negative Input and Target Labels with Different Sentiment Scores': count_n})
training_stats.update({'# of ambiguous Input and Target Labels with Different Sentiment Scores': count_a})
training_stats.update({'# of neutral Input and Target Labels with Different Sentiment Scores': count_e})

#print('Postive Input and Target Labels with Different Sentiment Scores: ' + str(count_p))
#print('Negative Input and Target Labels with Different Sentiment Scores: ' + str(count_n))
#print('Ambiguous Input and Target Labels with Different Sentiment Scores: ' + str(count_a))
#print('Neutral Input and Target Labels with Different Sentiment Scores: ' + str(count_e))

input_text      Tieto was no 17 on the list and received posit...
target_text     Tieto was not on the list 17 and received posi...
input_emo_g                                              positive
target_emo_g                                             positive
input_emo_e                                                   joy
target_emo_e                                                  joy
input_emo                                              admiration
target_emo                                               approval
input_sid                                                  0.7964
target_sid                                                 0.8519
Name: 2279, dtype: object
0.055499999999999994


input_text      The title track was a top-five single on the T...
target_text     The title track was a top five single on the T...
input_emo_g                                              positive
target_emo_g                                             positive
input_emo_e                

input_text      With the restoration of the monarchy and the f...
target_text     With the restoration of the monarchy and the f...
input_emo_g                                              positive
target_emo_g                                             positive
input_emo_e                                                   joy
target_emo_e                                              neutral
input_emo                                             realization
target_emo                                                neutral
input_sid                                                  0.4588
target_sid                                                 0.6808
Name: 15990, dtype: object
0.22199999999999998


input_text      According to the new doctrine, French principl...
target_text     According to new doctrine, French principles s...
input_emo_g                                              positive
target_emo_g                                             positive
input_emo_e                

input_text      A delicate teddy bear - similar creature, she ...
target_text     A harmless teddy bear like creature, she looks...
input_emo_g                                              positive
target_emo_g                                             positive
input_emo_e                                                   joy
target_emo_e                                                  joy
input_emo                                                 neutral
target_emo                                             admiration
input_sid                                                  0.8807
target_sid                                                 0.8294
Name: 23534, dtype: object
-0.05130000000000001


input_text      Each evening will be an optimistic celebration...
target_text     Every evening will be an intimate celebration ...
input_emo_g                                              positive
target_emo_g                                             positive
input_emo_e               

input_text      With the restoration of the monarchy and the f...
target_text     With the restoration of the monarchy and the f...
input_emo_g                                              positive
target_emo_g                                             positive
input_emo_e                                                   joy
target_emo_e                                              neutral
input_emo                                             realization
target_emo                                                neutral
input_sid                                                  0.6801
target_sid                                                 0.6808
Name: 39074, dtype: object
0.0006999999999999229


input_text      Without a big attacker, Garzelli was very cons...
target_text     Garzelli was very good without being a permane...
input_emo_g                                              positive
target_emo_g                                             positive
input_emo_e              

input_text           Make me famous, Make me
target_text     Make Me Famous, Make Me Rich
input_emo_g                         positive
target_emo_g                        positive
input_emo_e                          neutral
target_emo_e                             joy
input_emo                         excitement
target_emo                         curiosity
input_sid                                0.0
target_sid                            0.5574
Name: 46425, dtype: object
0.5574


input_text      SDT was the first team to earn the first, seco...
target_text     SDT was the first, second, third, fourth, fift...
input_emo_g                                              positive
target_emo_g                                             positive
input_emo_e                                               neutral
target_emo_e                                              neutral
input_emo                                             realization
target_emo                                          

...

input_text         What is the KVPY SA expected cut off for 2016?
target_text     What do you think the cutoff of KVPY 2016 SA w...
input_emo_g                                               neutral
target_emo_g                                              neutral
input_emo_e                                              surprise
target_emo_e                                             surprise
input_emo                                               curiosity
target_emo                                                neutral
input_sid                                                 -0.2732
target_sid                                                    0.0
Name: 127527, dtype: object
0.2732


input_text      How do people write huge 'questions' and also ...
target_text                      How can I add pictures on Quora?
input_emo_g                                               neutral
target_emo_g                                              neutral
input_emo_e                            

input_text         How is it like to touch huge boobs?
target_text     How does it feel when you press boobs?
input_emo_g                                    neutral
target_emo_g                                   neutral
input_emo_e                                    neutral
target_emo_e                                   neutral
input_emo                                    curiosity
target_emo                                     neutral
input_sid                                       0.5859
target_sid                                         0.0
Name: 134513, dtype: object
-0.5859


input_text      What is something you believe that almost nobo...
target_text     What is something you believe to be true that ...
input_emo_g                                               neutral
target_emo_g                                              neutral
input_emo_e                                               neutral
target_emo_e                                             surprise
input_emo       

input_text      Why do people ask questions on Quora instead o...
target_text     Why do people ask questions on Quora that are ...
input_emo_g                                               neutral
target_emo_g                                              neutral
input_emo_e                                               neutral
target_emo_e                                              neutral
input_emo                                                 neutral
target_emo                                              confusion
input_sid                                                     0.0
target_sid                                                -0.3691
Name: 142921, dtype: object
-0.3691


input_text      What are the security features of a new Rs. 50...
target_text     Why are some news channel and people saying th...
input_emo_g                                               neutral
target_emo_g                                              neutral
input_emo_e                           

input_text      Why do people ask questions on Quora instead o...
target_text     Why do people on Quora ask silly questions abo...
input_emo_g                                               neutral
target_emo_g                                              neutral
input_emo_e                                               neutral
target_emo_e                                              neutral
input_emo                                                 neutral
target_emo                                              curiosity
input_sid                                                     0.0
target_sid                                                 0.4201
Name: 149976, dtype: object
0.4201


input_text      Why do people ask questions on Quora that are ...
target_text     Why do some people ask questions on Quora that...
input_emo_g                                               neutral
target_emo_g                                              neutral
input_emo_e                            

input_text      What are some psychological tricks to get peop...
target_text     What are some psychological hacks/tricks to ge...
input_emo_g                                               neutral
target_emo_g                                              neutral
input_emo_e                                               neutral
target_emo_e                                             surprise
input_emo                                                 neutral
target_emo                                              curiosity
input_sid                                                    0.25
target_sid                                                 0.3612
Name: 157330, dtype: object
0.11120000000000002


input_text      Heavy hair falling, what should do to stop hai...
target_text                           How do I stop my hair fall?
input_emo_g                                               neutral
target_emo_g                                              neutral
input_emo_e               

In [53]:
count_p = 0 

for index, row in eval_df.iterrows():
    if (row.input_emo_g == 'positive') & (row.target_emo_g == 'positive'):
        if (row.input_emo != row.target_emo):
            diff = float(row.target_sid) - float(row.input_sid) 
            if (diff != 0.0): 
                print(row)
                print(diff)
                print('\n')
                count_p += 1 

count_n = 0
for index, row in eval_df.iterrows():
    if (row.input_emo_g == 'negative') & (row.target_emo_g == 'negative'):
        if (row.input_emo != row.target_emo):
            diff = float(row.target_sid) - float(row.input_sid) 
            if (diff != 0.0): 
                print(row)
                print(diff)
                print('\n')
                count_n += 1 

count_a = 0
for index, row in eval_df.iterrows():
    if (row.input_emo_g == 'ambiguous') & (row.target_emo_g == 'ambiguous'):
        if (row.input_emo != row.target_emo):
            diff = float(row.target_sid) - float(row.input_sid) 
            if (diff != 0.0): 
                print(row)
                print(diff)
                print('\n')
                count_a += 1 

count_e = 0
for index, row in eval_df.iterrows():
    if (row.input_emo_g == 'neutral') & (row.target_emo_g == 'neutral'):
        if (row.input_emo != row.target_emo):
            diff = float(row.target_sid) - float(row.input_sid) 
            if (diff != 0.0): 
                print(row)
                print(diff)
                print('\n')
                count_e += 1 

with open(f'compiled-data/{dataset_name}/{dataset_name}-testing_emo_si_stats.txt', 'a') as f:
    f.write('\n')
    f.write('# of postive Input and Target Labels with Different Sentiment Scores: ' + str(count_p))
    f.write('\n')
    f.write('# of negative Input and Target Labels with Different Sentiment Scores: ' + str(count_n))
    f.write('\n')
    f.write('# of ambiguous Input and Target Labels with Different Sentiment Scores: ' + str(count_a))
    f.write('\n')
    f.write('# of neutral Input and Target Labels with Different Sentiment Scores: ' + str(count_e))
    f.write('\n')

eval_stats.update({'# of Postive Input and Target Labels with Different Sentiment Scores': count_p})
eval_stats.update({'# of Negative Input and Target Labels with Different Sentiment Scores': count_n})
eval_stats.update({'# of Ambiguous Input and Target Labels with Different Sentiment Scores': count_a})
eval_stats.update({'# of Neutral Input and Target Labels with Different Sentiment Scores': count_e})

#print('Postive Input and Target Labels with Different Sentiment Scores: ' + str(count_p))
#print('Negative Input and Target Labels with Different Sentiment Scores: ' + str(count_n))
#print('Ambiguous Input and Target Labels with Different Sentiment Scores: ' + str(count_a))
#print('Neutral Input and Target Labels with Different Sentiment Scores: ' + str(count_e))

input_text      Christopher Griffiths ( born Christopher Llewe...
target_text     Christopher Llewellyn ( born Christopher Griff...
input_emo_g                                              positive
target_emo_g                                             positive
input_emo_e                                               neutral
target_emo_e                                                  joy
input_emo                                              admiration
target_emo                                                neutral
input_sid                                                  0.6369
target_sid                                                    0.0
Name: 20, dtype: object
-0.6369


input_text      Joan Milke Flores was inspiring and a friend o...
target_text     Nikki Hornsby was inspirational and to this da...
input_emo_g                                              positive
target_emo_g                                             positive
input_emo_e                               

input_text      Christopher Llewellyn ( born Christopher Griff...
target_text     Christopher Griffiths ( born Christopher Llewe...
input_emo_g                                              positive
target_emo_g                                             positive
input_emo_e                                               neutral
target_emo_e                                              neutral
input_emo                                                 neutral
target_emo                                             admiration
input_sid                                                     0.0
target_sid                                                 0.6369
Name: 7517, dtype: object
0.6369


input_text      The duo will continue to perform together acro...
target_text     The duo continue to perform and give workshops...
input_emo_g                                              positive
target_emo_g                                             positive
input_emo_e                              

input_text              What is the best joke you have heard?
target_text     Tell a joke that the funniest you have heard?
input_emo_g                                          positive
target_emo_g                                         positive
input_emo_e                                          surprise
target_emo_e                                         surprise
input_emo                                           curiosity
target_emo                                          amusement
input_sid                                              0.7506
target_sid                                             0.7003
Name: 39340, dtype: object
-0.05030000000000001


input_text      What is the best joke you've ever heard? Pleas...
target_text         Tell a joke that the funniest you have heard?
input_emo_g                                              positive
target_emo_g                                             positive
input_emo_e                                                   joy


input_text      How do I stop caring about what people think a...
target_text     How can I be indifferent to what people think ...
input_emo_g                                              negative
target_emo_g                                             negative
input_emo_e                                                 anger
target_emo_e                                             surprise
input_emo                                               annoyance
target_emo                                                neutral
input_sid                                                    0.25
target_sid                                                -0.2023
Name: 19868, dtype: object
-0.45230000000000004


input_text      What's the most annoying and unnecessary chara...
target_text     What's the most pathetic and unwanted characte...
input_emo_g                                              negative
target_emo_g                                             negative
input_emo_e               

input_text           What are some of the weirdest superstitions?
target_text     What are the weirdest and stupidest superstiti...
input_emo_g                                              negative
target_emo_g                                             negative
input_emo_e                                                 anger
target_emo_e                                                anger
input_emo                                               confusion
target_emo                                              annoyance
input_sid                                                 -0.2263
target_sid                                                -0.6486
Name: 34233, dtype: object
-0.42229999999999995


input_text      What is the most stupidest thing you have ever...
target_text     What is the most embarrassing thing you have e...
input_emo_g                                              negative
target_emo_g                                             negative
input_emo_e               

...

Name: 8697, dtype: object
0.4547


input_text      Voters in Cleveland Heights, Ohio, approved a ...
target_text     Voters in Cleveland Heights, Ohio, were asked ...
input_emo_g                                               neutral
target_emo_g                                              neutral
input_emo_e                                               neutral
target_emo_e                                              neutral
input_emo                                                approval
target_emo                                                neutral
input_sid                                                  0.4215
target_sid                                                 0.2263
Name: 8710, dtype: object
-0.19519999999999998


input_text      State air regulators and three automakers have...
target_text     State air regulators and three automakers have...
input_emo_g                                               neutral
target_emo_g                                              

input_text             How is it like to touch huge boobs?
target_text     How does it feel to touch a woman's boobs?
input_emo_g                                        neutral
target_emo_g                                       neutral
input_emo_e                                        neutral
target_emo_e                                      surprise
input_emo                                        curiosity
target_emo                                         neutral
input_sid                                           0.5859
target_sid                                             0.0
Name: 15804, dtype: object
-0.5859


input_text      What should be the URL to create blog on Quora?
target_text     How do you make the URL for your blog on Quora?
input_emo_g                                             neutral
target_emo_g                                            neutral
input_emo_e                                             neutral
target_emo_e                                         

input_text      What is the in hand salary of RBI grade B offi...
target_text     What is the impact that the 7th pay commission...
input_emo_g                                               neutral
target_emo_g                                              neutral
input_emo_e                                              surprise
target_emo_e                                              neutral
input_emo                                               curiosity
target_emo                                                neutral
input_sid                                                  0.4939
target_sid                                                -0.1027
Name: 28790, dtype: object
-0.5966


input_text          How do I get slim in a week?
target_text     How do you become slim and fair?
input_emo_g                              neutral
target_emo_g                             neutral
input_emo_e                             surprise
target_emo_e                            surprise
input_emo

input_text      Why do all of my questions get ignored on Quora?
target_text        Why are some questions not answered on Quora?
input_emo_g                                              neutral
target_emo_g                                             neutral
input_emo_e                                              neutral
target_emo_e                                             neutral
input_emo                                              confusion
target_emo                                               neutral
input_sid                                                -0.3182
target_sid                                                   0.0
Name: 36738, dtype: object
0.3182


input_text      What are the consequences of cutting a Pitbull...
target_text                         Should you crop Pitbull ears?
input_emo_g                                               neutral
target_emo_g                                              neutral
input_emo_e                                       

Name: 43688, dtype: object
-0.4215


input_text      Did you know <*/\*>1800*-251-*4919*-*<*/\*> Be...
target_text     Can I use this number //* [[1800*251*4919]] */...
input_emo_g                                               neutral
target_emo_g                                              neutral
input_emo_e                                               neutral
target_emo_e                                             surprise
input_emo                                                 neutral
target_emo                                              curiosity
input_sid                                                  0.4588
target_sid                                                 0.5228
Name: 44062, dtype: object
0.06400000000000006


input_text           Do bank PO get posting in their own Regions?
target_text     After selected in bank po can I get the postin...
input_emo_g                                               neutral
target_emo_g                                            

In [54]:
pos_inconsistency = 0 
neg_inconsistency = 0 
for index, row in train_df.iterrows():
    if ((row.input_emo_e in ['joy']) & (float(row.input_sid) < 0.0)) or \
        ((row.target_emo_e in ['joy']) & (float(row.target_sid) < 0.0)) :
        pos_inconsistency += 1
    if ((row.input_emo_e in ['anger', 'fear', 'sadness', 'disgust']) & (float(row.input_sid) > 0.0)) or \
        ((row.target_emo_e in ['anger', 'fear', 'sadness', 'disgust']) & (float(row.target_sid) > 0.0)):
        neg_inconsistency += 1

with open(f'compiled-data/{dataset_name}/{dataset_name}-training_emo_si_stats.txt', 'a') as f:
    f.write('\n')
    f.write('# of positive Ekmen emotion with negative sentiment score: ' + str(pos_inconsistency)  +  ' out of ' + str(train_df.size))
    f.write('\n')
    f.write('# of negative Ekmen emotion with positive sentiment score: ' + str(neg_inconsistency)  +  ' out of ' + str(train_df.size))
    f.write('\n')

training_stats.update({'# of positive Ekmen emotion with negative sentiment score': pos_inconsistency})
training_stats.update({'# of positive Ekmen emotion with negative sentiment score': neg_inconsistency})

#print('# of positive Ekmen emotion with negative sentiment score: ' + str(pos_inconsistency)  +  ' out of ' + str(train_df.size))
#print('# of negative Ekmen emotion with positive sentiment score: ' + str(neg_inconsistency)  +  ' out of ' + str(train_df.size))

In [55]:
pos_inconsistency = 0 
neg_inconsistency = 0 
for index, row in eval_df.iterrows():
    if ((row.input_emo_e in ['joy']) & (float(row.input_sid) < 0.0)) or \
        ((row.target_emo_e in ['joy']) & (float(row.target_sid) < 0.0)) :
        pos_inconsistency += 1
    if ((row.input_emo_e in ['anger', 'fear', 'sadness', 'disgust']) & (float(row.input_sid) > 0.0)) or \
        ((row.target_emo_e in ['anger', 'fear', 'sadness', 'disgust']) & (float(row.target_sid) > 0.0)):
        neg_inconsistency += 1

with open(f'compiled-data/{dataset_name}/{dataset_name}-testing_emo_si_stats.txt', 'a') as f:
    f.write('\n')
    f.write('# of positive Ekmen emotion with negative sentiment score: ' + str(pos_inconsistency)  +  ' out of ' + str(eval_df.size))
    f.write('\n')
    f.write('# of negative Ekmen emotion with positive sentiment score: ' + str(neg_inconsistency)  +  ' out of ' + str(eval_df.size))
    f.write('\n')

eval_stats.update({'# of positive Ekmen emotion with negative sentiment score': pos_inconsistency})
eval_stats.update({'# of positive Ekmen emotion with negative sentiment score': neg_inconsistency})

#print('# of positive Ekmen emotion with negative sentiment score: ' + str(pos_inconsistency)  +  ' out of ' + str(eval_df.size))
#print('# of negative Ekmen emotion with positive sentiment score: ' + str(neg_inconsistency)  +  ' out of ' + str(eval_df.size))

In [11]:
emotion_clusters = [ 
    ['anger', 'disgust', 'disapproval', 'annoyance'],
    ['love', 'joy', 'excitement', 'amusement'],
    ['desire', 'caring', 'optimism'],
    ['pride', 'admiration'],
    ['gratitude', 'relief'],
    ['approval', 'realization'],
    ['confusion', 'surprise', 'curiosity'],
    ['nervousness', 'fear', 'embarrassment', 'remorse'],
    ['disappointment', 'sadness', 'grief'],
    ['neutral']
]

emotion_transitions = {}

all_emotions = []
for cluster in emotion_clusters: 
    all_emotions += cluster
    for key in cluster: 
        if (key != 'neutral'):
            cluster_e = cluster + ['neutral']
            cluster_e.remove(key)
            emotion_transitions.update({key: cluster_e})

all_emotions.remove('neutral')
emotion_transitions.update({'neutral': all_emotions})

for item in emotion_transitions.items(): 
    print(item)

('anger', ['disgust', 'disapproval', 'annoyance', 'neutral'])
('disgust', ['anger', 'disapproval', 'annoyance', 'neutral'])
('disapproval', ['anger', 'disgust', 'annoyance', 'neutral'])
('annoyance', ['anger', 'disgust', 'disapproval', 'neutral'])
('love', ['joy', 'excitement', 'amusement', 'neutral'])
('joy', ['love', 'excitement', 'amusement', 'neutral'])
('excitement', ['love', 'joy', 'amusement', 'neutral'])
('amusement', ['love', 'joy', 'excitement', 'neutral'])
('desire', ['caring', 'optimism', 'neutral'])
('caring', ['desire', 'optimism', 'neutral'])
('optimism', ['desire', 'caring', 'neutral'])
('pride', ['admiration', 'neutral'])
('admiration', ['pride', 'neutral'])
('gratitude', ['relief', 'neutral'])
('relief', ['gratitude', 'neutral'])
('approval', ['realization', 'neutral'])
('realization', ['approval', 'neutral'])
('confusion', ['surprise', 'curiosity', 'neutral'])
('surprise', ['confusion', 'curiosity', 'neutral'])
('curiosity', ['confusion', 'surprise', 'neutral'])
('ne

In [ ]:
import numpy as np
import pandas as pd

train_df = pd.read_csv("compiled-data/mix/mix-training_emolabel_s.tsv", sep="\t").astype(str)

emotion_sids = {
    'admiration': [],
    'amusement': [],
    'anger': [],
    'annoyance': [],
    'approval': [],
    'caring': [],
    'confusion': [],
    'curiosity': [],
    'desire': [],
    'disappointment': [],
    'disapproval': [],
    'disgust': [],
    'embarrassment': [],
    'excitement': [],
    'fear': [],
    'gratitude': [],
    'grief': [],
    'joy': [],
    'love': [],
    'nervousness': [],
    'optimism': [],
    'pride': [],
    'realization': [],
    'relief': [],
    'remorse': [],
    'sadness': [],
    'surprise': [],
    'neutral': []
}

for index, row in train_df.iterrows(): 
    emotion_sids[row.input_emo].append(float(row.input_sid))
    emotion_sids[row.target_emo].append(float(row.target_sid))

print(emotion_sids) 

In [ ]:
# Median
import statistics as stats

emotion_median = {}

for key in emotion_sids:
    emotion_median[key] = stats.median(emotion_sids[key])

sort = {k: v for k, v in sorted(emotion_median.items(), key=lambda item: item[1])}

for item in sort:
    print(f'Emotion: {item}, Median: {sort[item]}')

In [56]:
GoEmo_SI = {
    'anger': -0.5234,
    'disgust': -0.5023,
    'grief': -0.4939,
    'fear': -0.4404,
    'sadness': -0.4404,
    'nervousness': -0.34,
    'annoyance': -0.296,
    'disappointment': -0.296, 
    'embarrassment': -0.24, 
    'remorse': -0.0772,
    'disapproval': -0.0644,
    'confusion': 0,
    'curiosity': 0,
    'realization': 0,
    'surprise': 0,
    'neutral': 0,
    'approval': 0.2846,
    'caring': 0.3412,
    'desire': 0.4019,
    'relief': 0.4391,
    'amusement': 0.4404,
    'excitement': 0.4404,
    'pride': 0.4767,
    'optimism': 0.4927,
    'gratitude': 0.5229,
    'joy': 0.5748,
    'admiration': 0.6004,
    'love': 0.6369
} 

pos_inconsistency = 0 
neg_inconsistency = 0 
for index, row in train_df.iterrows():
    if ((row.input_emo != 'neutral') | (row.target_emo != 'neutral')):
        if row.input_emo in emotion_transitions.keys() and row.target_emo in emotion_transitions[row.input_emo]:
            if (GoEmo_SI[row.input_emo] <  GoEmo_SI[row.target_emo]) & (float(row.input_sid) < float(row.target_sid)):
#            if (sort[row.input_emo] <  sort[row.target_emo]) & (float(row.input_sid) > float(row.target_sid)):
                pos_inconsistency += 1
                print(row)
            if (GoEmo_SI[row.input_emo] >  GoEmo_SI[row.target_emo]) & (float(row.input_sid) > float(row.target_sid)):
#            if (sort[row.input_emo] >  sort[row.target_emo]) & (float(row.input_sid) < float(row.target_sid)):
                neg_inconsistency += 1
                print(row)
        
with open(f'compiled-data/{dataset_name}/{dataset_name}-training_emo_si_stats.txt', 'a') as f:
    f.write('\n')
    f.write('# of emotions matching transition graphs and with increasing intensities: ' + str(pos_inconsistency))
    f.write('\n')
    f.write('# of emotions matching transition graphs and with decreasing intensities: ' + str(neg_inconsistency))

training_stats.update({'# of emotions matching transition graphs and with increasing intensities': pos_inconsistency})
training_stats.update({'# of emotions matching transition graphs and with decreasing intensities': neg_inconsistency})
          
pd_training_stats = pd.DataFrame(eval_stats.items(), columns=['Field', 'Value'])
pd_training_stats.to_csv(f'compiled-data/{dataset_name}/{dataset_name}-training_si_stats.tsv', sep="\t")

#print('# of matching emotion labels with rising sentiment intensities: ' + str(pos_inconsistency))
#print('# of matching emotion labels with droping sentiment intensities: ' + str(neg_inconsistency))

input_text      He became third in 1958 and 1967 at his table,...
target_text     He won first place at his table in 1958 and 19...
input_emo_g                                              positive
target_emo_g                                              neutral
input_emo_e                                                   joy
target_emo_e                                                  joy
input_emo                                                approval
target_emo                                            realization
input_sid                                                  0.7227
target_sid                                                 0.3291
Name: 167, dtype: object
input_text      There are a number of notable works in Afghan ...
target_text     There are a number of remarkable works in the ...
input_emo_g                                               neutral
target_emo_g                                             positive
input_emo_e                                        

input_text      The American mission in Stockholm, Sweden, als...
target_text     The American Legation in Stockholm, Sweden, al...
input_emo_g                                               neutral
target_emo_g                                              neutral
input_emo_e                                               neutral
target_emo_e                                              neutral
input_emo                                                approval
target_emo                                                neutral
input_sid                                                  0.5267
target_sid                                                 0.3182
Name: 6928, dtype: object
input_text      Abraham Salomon Gluck was probably killed on o...
target_text     Abraham Salomon Gluck was alike murdered, prob...
input_emo_g                                               neutral
target_emo_g                                              neutral
input_emo_e                                       

input_text      William and Elizabeth died the following year ...
target_text     In 1859, Elizabeth died and William died the f...
input_emo_g                                              negative
target_emo_g                                             negative
input_emo_e                                               neutral
target_emo_e                                              neutral
input_emo                                                 neutral
target_emo                                                sadness
input_sid                                                 -0.5574
target_sid                                                 -0.802
Name: 13463, dtype: object
input_text      Of these, the Austin Catholic Academy and St. ...
target_text     Of these, Austin Catholic Academy and St. Thom...
input_emo_g                                               neutral
target_emo_g                                              neutral
input_emo_e                                      

input_text      While it is fully turing-practical, it is not ...
target_text     While it is fully Turing-complete, it is not i...
input_emo_g                                              positive
target_emo_g                                                  nan
input_emo_e                                               neutral
target_emo_e                                              neutral
input_emo                                                 neutral
target_emo                                              amusement
input_sid                                                  0.5267
target_sid                                                 0.6124
Name: 19928, dtype: object
input_text      Roan Carneiro faced LaFlare on February 11, 20...
target_text     LaFlare confronted Roan Carneiro at UFC 208 on...
input_emo_g                                               neutral
target_emo_g                                              neutral
input_emo_e                                      

input_text      Without a big attacker, Garzelli was very cons...
target_text     Garzelli, without being a permanent attacker, ...
input_emo_g                                              positive
target_emo_g                                             positive
input_emo_e                                                   joy
target_emo_e                                                  joy
input_emo                                                 neutral
target_emo                                             admiration
input_sid                                                  0.8778
target_sid                                                 0.9381
Name: 26338, dtype: object
input_text      The Sultan of Golconda accepted and attacked M...
target_text     The Sultan of Golconda accepted and attacked M...
input_emo_g                                              negative
target_emo_g                                             positive
input_emo_e                                      

...

input_text      What is the most tactless thing you have ever ...
target_text      What was the rudest thing you have said or done?
input_emo_g                                               neutral
target_emo_g                                             negative
input_emo_e                                              surprise
target_emo_e                                                anger
input_emo                                                 neutral
target_emo                                                  anger
input_sid                                                     0.0
target_sid                                                -0.5423
Name: 107936, dtype: object
input_text         What could be the stupidest question in Quora?
target_text     What are the worst stupidest questions asked o...
input_emo_g                                               neutral
target_emo_g                                             negative
input_emo_e                                     

input_text      Why do people ask such stupid questions on Quora?
target_text     Why are there so many pointless questions on Q...
input_emo_g                                              negative
target_emo_g                                            ambiguous
input_emo_e                                               neutral
target_emo_e                                              neutral
input_emo                                               annoyance
target_emo                                                neutral
input_sid                                                 -0.5267
target_sid                                                    0.0
Name: 125371, dtype: object
input_text        What is the stupidest thing you have ever done?
target_text     What is the dumbest thing that you have ever d...
input_emo_g                                              negative
target_emo_g                                             negative
input_emo_e                                     

input_text      How do you post question in Quora? I posted ma...
target_text                    How do I post a question in quora?
input_emo_g                                              negative
target_emo_g                                              neutral
input_emo_e                                              surprise
target_emo_e                                              neutral
input_emo                                             disapproval
target_emo                                                neutral
input_sid                                                 -0.6652
target_sid                                                    0.0
Name: 136231, dtype: object
input_text          Can you work under pressure?
target_text     Do you work well under pressure?
input_emo_g                            ambiguous
target_emo_g                           ambiguous
input_emo_e                             surprise
target_emo_e                            surprise
input_emo         

input_text      Secrets: What terrible thing did you do, that ...
target_text     What is a secret you would not tell anyone but...
input_emo_g                                              negative
target_emo_g                                              neutral
input_emo_e                                                  fear
target_emo_e                                              neutral
input_emo                                                    fear
target_emo                                                neutral
input_sid                                                 -0.4767
target_sid                                                    0.0
Name: 148194, dtype: object
input_text      What is the worst thing you saw your kids do t...
target_text     What is one thing that you saw your daughter d...
input_emo_g                                                   nan
target_emo_g                                              neutral
input_emo_e                                     

input_text      Why do people put ridiculous questions on Quor...
target_text     Do people post questions in Quora just so that...
input_emo_g                                              negative
target_emo_g                                              neutral
input_emo_e                                                 anger
target_emo_e                                              neutral
input_emo                                               annoyance
target_emo                                                neutral
input_sid                                                 -0.5719
target_sid                                                    0.0
Name: 163210, dtype: object
input_text      What is the most stupid thing you have ever done?
target_text     What is the dumbest thing that you have ever d...
input_emo_g                                              negative
target_emo_g                                             negative
input_emo_e                                     

In [ ]:
import numpy as np
import pandas as pd

eval_df = pd.read_csv("compiled-data/mix/mix-testing_emolabel_s.tsv", sep="\t").astype(str)

emotion_sids = {
    'admiration': [],
    'amusement': [],
    'anger': [],
    'annoyance': [],
    'approval': [],
    'caring': [],
    'confusion': [],
    'curiosity': [],
    'desire': [],
    'disappointment': [],
    'disapproval': [],
    'disgust': [],
    'embarrassment': [],
    'excitement': [],
    'fear': [],
    'gratitude': [],
    'grief': [],
    'joy': [],
    'love': [],
    'nervousness': [],
    'optimism': [],
    'pride': [],
    'realization': [],
    'relief': [],
    'remorse': [],
    'sadness': [],
    'surprise': [],
    'neutral': []
}

for index, row in eval_df.iterrows(): 
    emotion_sids[row.input_emo].append(float(row.input_sid))
    emotion_sids[row.target_emo].append(float(row.target_sid))

print(emotion_sids) 

In [ ]:
# Median
import statistics as stats

emotion_median = {}

for key in emotion_sids:
    if (len(emotion_sids[key]) != 0):
        emotion_median[key] = stats.median(emotion_sids[key])
    else:
        emotion_median[key] = float('NaN')

sort = {k: v for k, v in sorted(emotion_median.items(), key=lambda item: item[1])}

for item in sort:
    print(f'Emotion: {item}, Median: {sort[item]}')

In [57]:
GoEmo_SI = {
    'anger': -0.5234,
    'disgust': -0.5023,
    'grief': -0.4939,
    'fear': -0.4404,
    'sadness': -0.4404,
    'nervousness': -0.34,
    'annoyance': -0.296,
    'disappointment': -0.296, 
    'embarrassment': -0.24, 
    'remorse': -0.0772,
    'disapproval': -0.0644,
    'confusion': 0,
    'curiosity': 0,
    'realization': 0,
    'surprise': 0,
    'neutral': 0,
    'approval': 0.2846,
    'caring': 0.3412,
    'desire': 0.4019,
    'relief': 0.4391,
    'amusement': 0.4404,
    'excitement': 0.4404,
    'pride': 0.4767,
    'optimism': 0.4927,
    'gratitude': 0.5229,
    'joy': 0.5748,
    'admiration': 0.6004,
    'love': 0.6369
} 

pos_inconsistency = 0 
neg_inconsistency = 0 
for index, row in eval_df.iterrows():
    if ((row.input_emo != 'neutral') | (row.target_emo != 'neutral')):
        if row.input_emo in emotion_transitions.keys() and row.target_emo in emotion_transitions[row.input_emo]:
            if (GoEmo_SI[row.input_emo] <  GoEmo_SI[row.target_emo]) & (float(row.input_sid) < float(row.target_sid)):
#            if (sort[row.input_emo] <  sort[row.target_emo]) & (float(row.input_sid) > float(row.target_sid)):
                pos_inconsistency += 1
                print(row)
            if (GoEmo_SI[row.input_emo] >  GoEmo_SI[row.target_emo]) & (float(row.input_sid) > float(row.target_sid)):
#            if (sort[row.input_emo] >  sort[row.target_emo]) & (float(row.input_sid) < float(row.target_sid)):
                neg_inconsistency += 1
                print(row)

with open(f'compiled-data/{dataset_name}/{dataset_name}-testing_emo_si_stats.txt', 'a') as f:
    f.write('\n')
    f.write('# of emotions matching transition graphs and with increasing intensities: ' + str(pos_inconsistency))
    f.write('\n')
    f.write('# of emotions matching transition graphs and with decreasing intensities: ' + str(neg_inconsistency))

eval_stats.update({'# of emotions matching transition graphs and with increasing intensities': pos_inconsistency})
eval_stats.update({'# of emotions matching transition graphs and with decreasing intensities': neg_inconsistency})

pd_eval_stats = pd.DataFrame(eval_stats.items(), columns=['Field', 'Value'])
pd_eval_stats.to_csv(f'compiled-data/{dataset_name}/{dataset_name}-testing_si_stats.tsv', sep="\t")

#print('# of matching emotion labels with rising sentiment intensities: ' + str(pos_inconsistency))
#print('# of matching emotion labels with droping sentiment intensities: ' + str(neg_inconsistency))

input_text      Christopher Griffiths ( born Christopher Llewe...
target_text     Christopher Llewellyn ( born Christopher Griff...
input_emo_g                                              positive
target_emo_g                                             positive
input_emo_e                                               neutral
target_emo_e                                                  joy
input_emo                                              admiration
target_emo                                                neutral
input_sid                                                  0.6369
target_sid                                                    0.0
Name: 20, dtype: object
input_text      The Chilean New Song movement was encouraged i...
target_text     The Chilean New Song movement was fired by the...
input_emo_g                                               neutral
target_emo_g                                              neutral
input_emo_e                                         

input_text      They do not follow the pattern of caldera - gr...
target_text     They do not follow the pattern of caldera grow...
input_emo_g                                               neutral
target_emo_g                                              neutral
input_emo_e                                               neutral
target_emo_e                                              neutral
input_emo                                                 neutral
target_emo                                            disapproval
input_sid                                                  0.1152
target_sid                                                  -0.25
Name: 4982, dtype: object
input_text      This neurological disorder is aggravated by a ...
target_text     This neurological disorder is caused by a lack...
input_emo_g                                              negative
target_emo_g                                             negative
input_emo_e                                       

input_text      What one song makes you cry and smile at the s...
target_text     What are some emotional song that can make you...
input_emo_g                                              negative
target_emo_g                                            ambiguous
input_emo_e                                               sadness
target_emo_e                                             surprise
input_emo                                                 sadness
target_emo                                                neutral
input_sid                                                 -0.1531
target_sid                                                    0.0
Name: 10719, dtype: object
input_text      What is that one thing you regret the most and...
target_text     If you could change one thing about the past w...
input_emo_g                                             ambiguous
target_emo_g                                            ambiguous
input_emo_e                                      

input_text      I never signed up for this Quora account. How ...
target_text          How can I delete this account? Please answer
input_emo_g                                             ambiguous
target_emo_g                                            ambiguous
input_emo_e                                              surprise
target_emo_e                                             surprise
input_emo                                             disapproval
target_emo                                                neutral
input_sid                                                     0.0
target_sid                                                 0.3182
Name: 23362, dtype: object
input_text      Why do people put ridiculous questions on Quor...
target_text     Why do people bother to ask questions on Quora...
input_emo_g                                              negative
target_emo_g                                              neutral
input_emo_e                                      

input_text      I am facing problem with my TalkTalk broadband...
target_text                  How do you report Fault to TalkTalk?
input_emo_g                                              negative
target_emo_g                                            ambiguous
input_emo_e                                               sadness
target_emo_e                                             surprise
input_emo                                               annoyance
target_emo                                                neutral
input_sid                                                 -0.6597
target_sid                                                -0.4019
Name: 38365, dtype: object
input_text      Why are so many Quora questions about factual ...
target_text     Why do people ask stupid questions on Quora th...
input_emo_g                                               neutral
target_emo_g                                             negative
input_emo_e                                      

In [ ]:
for index, row in train_df.iterrows():
    if (row.input_emo_g == 'positive') & (float(row.input_sid) < 0.0):
        train_df.drop(index, inplace=True)
    if (row.input_emo_g == 'negative') & (float(row.input_sid) > 0.0):
        train_df.drop(index, inplace=True)

In [ ]:
for index, row in eval_df.iterrows():
    if (row.input_emo_g == 'positive') & (float(row.input_sid) < 0.0):
        eval_df.drop(index, inplace=True)
    if (row.input_emo_g == 'negative') & (float(row.input_sid) > 0.0):
        eval_df.drop(index, inplace=True)